In [1]:
!pip install folium requests

In [2]:
import folium
import requests
import json

In [3]:
# URL to the USGS GeoJSON feed
url = "https://earthquake.usgs.gov/earthquakes/feed/v1.0/summary/all_week.geojson"

# Fetch the data
response = requests.get(url)
data = response.json()

In [4]:
# Initialize the map centered at an approximate center of the dataset
map_center = [20, 0]
earthquake_map = folium.Map(location=map_center, zoom_start=2)


In [5]:
def get_color(depth):
    if depth > 90:
        return '#d73027'
    elif depth > 70:
        return '#fc8d59'
    elif depth > 50:
        return '#fee08b'
    elif depth > 30:
        return '#d9ef8b'
    elif depth > 10:
        return '#91cf60'
    else:
        return '#1a9850'

def get_radius(magnitude):
    return magnitude * 4

In [6]:
for feature in data['features']:
    coords = feature['geometry']['coordinates']
    lon, lat, depth = coords[0], coords[1], coords[2]
    mag = feature['properties']['mag']
    place = feature['properties']['place']
    time = feature['properties']['time']

    # Create the marker
    folium.CircleMarker(
        location=[lat, lon],
        radius=get_radius(mag),
        color='black',
        fill=True,
        fill_color=get_color(depth),
        fill_opacity=0.7,
        popup=f"Location: {place}<br>Magnitude: {mag}<br>Depth: {depth} km"
    ).add_to(earthquake_map)

In [7]:
from branca.element import Template, MacroElement

template = """
{% macro html(this, kwargs) %}
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 150px;
    height: 220px;
    background-color: white;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
">
&nbsp; <b>Depth (km)</b> <br>
&nbsp; <i style="background: #1a9850"></i>&nbsp; -10-10 <br>
&nbsp; <i style="background: #91cf60"></i>&nbsp; 10-30 <br>
&nbsp; <i style="background: #d9ef8b"></i>&nbsp; 30-50 <br>
&nbsp; <i style="background: #fee08b"></i>&nbsp; 50-70 <br>
&nbsp; <i style="background: #fc8d59"></i>&nbsp; 70-90 <br>
&nbsp; <i style="background: #d73027"></i>&nbsp; 90+ <br>
</div>
{% endmacro %}
"""

macro = MacroElement()
macro._template = Template(template)
earthquake_map.get_root().add_child(macro)

In [8]:
earthquake_map

In [9]:
# URL to the tectonic plates GeoJSON data
tectonic_plates_url = "https://raw.githubusercontent.com/fraxen/tectonicplates/master/GeoJSON/PB2002_boundaries.json"

# Fetch the data
tectonic_plates_response = requests.get(tectonic_plates_url)
tectonic_plates_data = tectonic_plates_response.json()

# Add tectonic plates layer to the map
folium.GeoJson(
    tectonic_plates_data,
    style_function=lambda x: {'color': 'orange', 'weight': 2}
).add_to(earthquake_map)

In [10]:
folium.LayerControl().add_to(earthquake_map)

In [11]:
earthquake_map